In [2]:
# -*- coding:utf-8 -*-
'''
Created on 2020年2月15日

@author: zfl
'''
from lxml import html
import requests
import json
import re
import pymssql
from datetime import datetime
import requests
from lxml import etree
import os
import pandas as pd
from selenium import webdriver
import pandas as pd
import datetime
import re
import time
import os
from selenium.webdriver.common.keys import Keys

D:\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: DeprecationWarning: Using or importing the ABCs from 'collections' instead of from 'collections.abc' is deprecated, and in 3.8 it will stop working
  # This is added back by InteractiveShellApp.init_path()


In [3]:
os.chdir(r"D:/graduate_student/2020spring/案例大赛")

# 热搜关键词爬取

本部分主要是在https://www.weibotop.cn/ 网址上爬取每天的微博热搜关键字

In [3]:
chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument("--headless")
chrome_options.add_argument('--disable-gpu')
chrome_options.add_argument("window-size=1024,768")
chrome_options.add_argument("--no-sandbox")
LEFT = '\ue012'  #左键
new_driver = webdriver.Chrome()
url = "https://www.weibotop.cn/"
year = datetime.datetime.now().year
month = datetime.datetime.now().month
day = datetime.datetime.now().day
try:
    new_driver.get(url)
except:
    print("the url is error")
resou = pd.DataFrame(columns = {"time","news_title","first","final","onlist"})
pages = 50
id = 0
newslist = 50
for j in range(pages):
    print("This is the"+str(j)+"page")
    for i in range(newslist):
        news_order = i+1
        print(i)
        resou.at[id,'news_title']=new_driver.find_element_by_xpath('//*[@id="container"]/div['+str(news_order)+']/p[1]').text
        resou.at[id,'time']=new_driver.find_element_by_xpath('//*[@id="show_timestamp"]').text
        resou.at[id,'first']=new_driver.find_element_by_xpath('//*[@id="container"]/div['+str(news_order)+']/p[2]').text
        resou.at[id,'final']=new_driver.find_element_by_xpath('//*[@id="container"]/div['+str(news_order)+']/p[3]').text
        resou.at[id,'onlist']=new_driver.find_element_by_xpath('//*[@id="container"]/div['+str(news_order)+']/p[4]').text
        id = id+1
    new_driver.find_element_by_xpath('/html/body/div[1]/div[1]/div[2]/div/a').send_keys(Keys.LEFT)

This is the0page
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
This is the1page
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
This is the2page
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
This is the3page
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
This is the4page
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
This is the5page
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
This is the6page
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16


将爬取到的内容以csv格式存储

In [4]:
resou.to_csv("resou.csv",encoding = "GBK")

# 微博评论爬取

在本节中将会对每一个热搜爬取相应的评论点赞，然后获取那种评论数大于500的博文，最大的爬取博文数量为20，一个博文下的前500个评论信息，这样一个热搜就可以有10000条评论信息

In [21]:
resou = pd.read_csv("resou.csv",encoding = "GBK")

In [5]:
resouList = resou.iloc[:,1:6]

In [22]:
resou

Unnamed: 0            onlist                     final  \
0              0   在榜时长：09小时54分00秒  最后时间：2020-03-02 07:42:01   
1              1   在榜时长：00小时22分00秒  最后时间：2020-03-02 07:42:01   
2              2   在榜时长：00小时33分59秒  最后时间：2020-03-02 07:42:01   
3              3   在榜时长：10小时41分59秒  最后时间：2020-03-02 07:42:01   
4              4   在榜时长：09小时18分00秒  最后时间：2020-03-02 07:42:01   
...          ...               ...                       ...   
2495        2495   在榜时长：11小时58分00秒  最后时间：2019-12-30 08:30:02   
2496        2496  在榜时长：872小时36分01秒  最后时间：2019-12-30 07:56:02   
2497        2497   在榜时长：11小时35分59秒  最后时间：2019-12-30 07:34:01   
2498        2498   在榜时长：17小时10分00秒  最后时间：2019-12-30 07:30:02   
2499        2499   在榜时长：08小时22分00秒  最后时间：2019-12-30 07:22:02   

                     time         news_title                     first  
0     2020-03-02 07:42:01          1.肖战工作室道歉  上榜时间：2020-03-01 21:48:01  
1     2020-03-02 07:42:01    2.意大利新增566例新冠肺炎  上榜时间：2020-03-02 07:20:01  
2     2020-03-02 07:42:01            3.武磊造乌龙  上榜时间：2020-03-02 07:08:02  
3     2020-03-02 07:42:01            4.上海老洋房  上榜时间：2020-03-01 21:00:02  
4     2020-03-02 07:42:01  5.深圳新增由英国途经香港输入病例  上榜时间：2020-03-01 22:24:01  
...                   ...                ...                       ...  
2495  2019-12-30 07:20:02     46.少儿散打的爆笑打开方式  上榜时间：2019-12-29 20:32:02  
2496  2019-12-30 07:20:02         47.eStar赢了  上榜时间：2019-11-23 23:20:01  
2497  2019-12-30 07:20:02            48.周琦受伤  上榜时间：2019-12-29 19:58:02  
2498  2019-12-30 07:20:02         49.女生眼中的腿精  上榜时间：2019-12-29 14:20:02  
2499  2019-12-30 07:20:02         50.阿森纳 切尔西  上榜时间：2019-12-29 23:00:02  

[2500 rows x 6 columns]

In [7]:
#把每一个热搜前的标号去除一下
for k in range(resouList.shape[0]):
    resouList.at[k,'news_title'] = re.sub(r'[0-9]+\.','',resouList.at[k,'news_title'])

In [ ]:
#这里说明一下，只取官方发送的推文为事件关键点，默认取第一个热门推文,选取第一个热门推文中的所有评论（5000+）作为网民情绪分析来源
#new_driver = webdriver.Chrome()
#pinglun = pd.DataFrame(columns = {"time","news_title","review"})
#i = 128 #序号，表示第几个热搜
k = 26347
#flag = 1 #表示重新开始一个session
for m in range(566,len(resouList.news_title)):
    time1 = time.time()
    title = resouList.news_title[m]
    if title =='（微博广告位留空）':
        continue
    print("这是对"+str(title)+"的评论获取")
    url = "https://s.weibo.com/weibo?q="+str(title)+"&xsort=hot&Refer=hotmore"
    try:
        new_driver.get(url)
    except:
        print("the url is error")
    #theme_len = len(new_driver.find_elements_by_class_name("card-wrap"))
    #resouList.at[i,'theme'] = new_driver.find_element_by_xpath("//*[@id='pl_feedlist_index']/div[2]/div[1]/div/div[1]/div[2]/p[2]").text
    #my_str = new_driver.find_element_by_xpath('//*[@id="pl_feedlist_index"]/div[2]/div[1]/div/div[2]/ul/li[3]/a').text    
   
    review_len = 200##只爬取前1000个评论信息    
    if(flag==0):
        time.sleep(5)
        new_driver.find_element_by_xpath('//*[@id="weibo_top_public"]/div/div/div[3]/div[2]/ul/li[3]/a').click()
        time.sleep(5)#等待着登录框跳出来
        new_driver.find_element_by_name('username').send_keys("18811399396")
        new_driver.find_element_by_name('password').send_keys("980zfl+-")
        new_driver.find_element_by_class_name('W_btn_a').click()
        flag = 1
        time.sleep(10)#等待着登录
    time.sleep(5)
    for section in range(1,5):
        try:
            new_driver.execute_script('window.scrollTo(0,1000)')
            new_driver.find_element_by_xpath('//*[@id="pl_feedlist_index"]/div[2]/div['+str(section)+']/div/div[2]/ul/li[3]/a').click()
            print("到底有没有抓啊")
            time.sleep(3)
            new_driver.execute_script('window.scrollTo(0,1000)') 
            new_driver.find_element_by_xpath('//*[@id="pl_feedlist_index"]/div[2]/div['+str(section)+']/div/div[3]/div/div[3]/a/i').click()
        except:
            continue
    #new_driver.get(href)
    #将滚动条移动到页面的底部
        new_driver.execute_script('window.scrollTo(0,1000000)') 
        time.sleep(10)
        lens = len(new_driver.find_elements_by_class_name("list_li"))
        for j in range(review_len):
            pinglun.at[k,'time'] = m
            pinglun.at[k,'news_title'] = m
            order = j+1
            try:
                print("这是第"+str(j)+"条评论")
                pinglun.at[k,'review'] = new_driver.find_element_by_xpath('//div[@node-type="comment_list"]/div['+str(order)+']/div[2]/div[1]').text
                k = k+1
            except:
                new_driver.execute_script('window.scrollTo(0,1000000)') 
                time.sleep(3)
                try:
                    new_driver.execute_script('window.scrollTo(0,1000000)')
                    time.sleep(3)
                    new_driver.find_element_by_class_name("more_txt").click()
                except:
                    break
            
        new_driver.get(url)            
    i = i+1
    print("用时"+str(time.time()-time1))

# 微博主题爬取

本节中将会对某一个热搜对应的博主发文进行爬取，用于主题词的提取

In [6]:
#把标号去除一下
for k in range(resou_new.shape[0]):
    resou_new.at[k,'news_title'] = re.sub(r'[0-9]+\.','',resou_new.at[k,'news_title'])

In [8]:
#这里说明一下，只取官方发送的推文为事件关键点，默认取第一个热门推文,选取第一个热门推文中的所有评论（5000+）作为网民情绪分析来源
new_driver = webdriver.Chrome()
theme = pd.DataFrame(columns = {"time","news_title","news_theme"})
i = 0 #序号，表示第几个热搜
k = 1
flag = 1 #表示重新开始一个session
for m in range(0,len(resou_new.news_title)):
    time1 = time.time()
    title = resou_new.news_title[m]
    if title =='（微博广告位留空）':
        continue
    print("这是对"+str(m)+"个"+str(title)+"的主题获取")
    url = "https://s.weibo.com/weibo?q="+str(title)+"&xsort=hot&Refer=hotmore"
    time.sleep(2)
    try:
        new_driver.get(url)
    except:
        print("the url is error")
    try:
        theme.at[m,'news_theme'] = new_driver.find_element_by_xpath("//*[@id='pl_feedlist_index']/div[2]/div[1]/div/div[1]/div[2]/p[1]").text
    except:
        try:
            time.sleep(5)
            new_driver.find_element_by_name('username').send_keys("18811399396")
            new_driver.find_element_by_name('password').send_keys("980zfl+-")
            new_driver.find_element_by_class_name('W_btn_a').click()
            time.sleep(5)#等待着登录框跳出来
        except:
            continue
    theme.at[m,'time'] = m
    theme.at[m,'news_title'] = m
    print("用时"+str(time.time()-time1))

这是对0个肖战工作室道歉的主题获取
用时4.136753797531128
这是对1个意大利新增566例新冠肺炎的主题获取
用时3.161529064178467
这是对2个武磊造乌龙的主题获取
用时2.9923195838928223
这是对3个上海老洋房的主题获取
用时3.725830554962158
这是对4个深圳新增由英国途经香港输入病例的主题获取
用时3.1201171875
这是对5个周深 少管我的主题获取
用时3.260002613067627
这是对6个意大利居民拒戴口罩要自由的主题获取
用时4.04001259803772
这是对7个江达琳的脑子的主题获取
用时3.3399789333343506
这是对8个全面暂停离汉离鄂网约车业务的主题获取
用时2.972548723220825
这是对9个韩国首次证实新天地教徒到过武汉的主题获取
用时3.1046528816223145
这是对10个何炅做麻辣烫的主题获取
用时3.5802083015441895
这是对11个天天向上的主题获取
用时3.1707839965820312
这是对12个李现刮胡子前后的主题获取
用时3.5102598667144775
这是对13个36岁医生抗疫时心脏骤停去世的主题获取
用时3.0435328483581543
这是对14个安家的主题获取
用时3.0151164531707764
这是对15个日本网友用中文表达感谢的主题获取
用时3.9264628887176514
这是对16个生活中突然崩溃的经历的主题获取
用时2.925266742706299
这是对17个肖战后援会道歉的主题获取
用时3.350677967071533
这是对18个雷神山医院里的钟南山漫画的主题获取
用时3.223472833633423
这是对19个像极了儿时家人给你脱衣服的主题获取
用时3.0428171157836914
这是对20个单身率特别高的大学专业的主题获取
用时3.0837714672088623
这是对21个开学的主题获取
用时2.9218356609344482
这是对22个剑网三的主题获取
用时3.0664939880371094
这是对23个这次疫情让你看到了什么的主题获取
用时2.9200170040130615
这是对24个白凯南节目的主题获取
用时3.1650

用时2.924494981765747
这是对196个皇马1-2曼城的主题获取
用时3.906132221221924
这是对197个白岩松谈武汉来京女子确诊新冠肺炎的主题获取
用时3.086137533187866
这是对198个芬兰确诊2例新冠肺炎病例的主题获取
用时2.8237452507019043
这是对199个大学生14种语言制作抗疫视频的主题获取
用时3.0535848140716553
这是对200个浙江10万只鸭子出征巴基斯坦灭蝗的主题获取
用时3.0658833980560303
这是对201个美国现首例无法确定病源新冠肺炎患者的主题获取
用时3.4251959323883057
这是对202个北京电影院隔排隔座售票的主题获取
用时2.967412233352661
这是对203个全国人民超长假期缩影的主题获取
用时3.5931646823883057
这是对204个特朗普称新冠病毒风险对美国依旧很低的主题获取
用时3.069916009902954
这是对205个韩国新冠肺炎累计1595例的主题获取
用时3.0839405059814453
这是对206个王毅同日韩外长通电话的主题获取
用时3.1217939853668213
这是对207个林青霞写信致敬前线抗疫英雄的主题获取
用时3.1294641494750977
这是对208个31省区市新增433例新冠肺炎的主题获取
用时3.267890453338623
这是对209个崔娃谈特朗普访印当场笑抽的主题获取
用时3.09879207611084
这是对210个德国出现士兵感染的主题获取
用时3.01682448387146
这是对211个粉丝绸的主题获取
用时3.0790693759918213
这是对212个湖北彻查刑释确诊人员离汉抵京的主题获取
用时3.0224740505218506
这是对213个东京奥运会火炬接力考虑缩小规模的主题获取
用时3.043715238571167
这是对214个张家口新增5例新冠肺炎的主题获取
用时2.9381844997406006
这是对215个iPhoneXR出货量全球第一的主题获取
用时3.100032091140747
这是对216个李佳琦小助理的主题获取
用时3.791377544403076
这是对217个十堰老人家中死亡留下6岁孙子的主

用时3.355421781539917
这是对386个韩总统府十几名内部警卫被隔离的主题获取
用时2.8824400901794434
这是对387个北京一确诊病例复工期间密切接触66人的主题获取
用时3.0152063369750977
这是对388个7类返京人群免隔离14天的主题获取
用时3.04571533203125
这是对389个高三班主任直播中数次落泪的主题获取
用时2.9722211360931396
这是对390个汪小菲说大S短发是洗剪吹的主题获取
用时3.1327600479125977
这是对391个新疆伽师1级地震的主题获取
这是对392个湖北订正19日确诊病例数的主题获取
用时3.2658395767211914
这是对393个世卫组织专家小组周六前往武汉的主题获取
用时2.9499406814575195
这是对394个中共中央政治局研究疫情防控工作的主题获取
用时2.9391086101531982
这是对395个炼乳草莓的主题获取
用时2.978403329849243
这是对396个打工夫妻治愈后携手捐血浆的主题获取
用时2.942840576171875
这是对397个心疼景辞的主题获取
用时3.1551642417907715
这是对398个女生化妆出门的真实原因的主题获取
用时3.169666290283203
这是对399个难听的主题获取
用时3.062669277191162
这是对400个护士杜富佳的主题获取
用时2.915661334991455
这是对401个核酸阴性不能排除新冠感染的主题获取
用时2.92535662651062
这是对403个全国疫情发展拐点尚未到来的主题获取
用时2.9423532485961914
这是对404个何炅做双皮奶的主题获取
用时3.212196111679077
这是对405个因封路在面包车上生存26天的主题获取
用时2.9965579509735107
这是对406个宁桓宇结婚的主题获取
用时2.9713072776794434
这是对407个火锅外卖的主题获取
用时3.0953054428100586
这是对408个馒头披萨的主题获取
用时3.0189170837402344
这是对409个金海没死的主题获取
用时3.3027515411376953
这是对410个以为每天上传体

用时3.0492241382598877
这是对581个龙港的主题获取
用时3.089625597000122
这是对582个贺妈妈发现贺灿阳蔡敏敏恋爱的主题获取
用时3.232839584350586
这是对583个湖北以外新增确诊病例12连降的主题获取
用时3.3071982860565186
这是对584个女生睡觉时的样子的主题获取
用时3.0706465244293213
这是对585个厦门消毒的主题获取
用时3.2225754261016846
这是对586个医生甘如意用4天3夜返回武汉一线的主题获取
用时3.109968900680542
这是对587个湖北电影制片厂常凯因新冠肺炎去世的主题获取
用时3.1243269443511963
这是对588个饺子 李现实在太帅了的主题获取
用时3.311694622039795
这是对589个首个潜在治疗新冠肺炎药物获批上市的主题获取
用时3.201563596725464
这是对590个BTS新歌和Sia合作的主题获取
用时3.286489248275757
这是对591个郑爽康辉合影的主题获取
用时3.134150743484497
这是对592个刘柏辛模仿台湾腔的主题获取
用时3.1642022132873535
这是对593个武汉将开展拉网式大排查的主题获取
用时3.0503828525543213
这是对594个军队物资仓库有多让人安心的主题获取
用时3.0288257598876953
这是对595个贫穷让我躲过了一劫的主题获取
用时3.240758180618286
这是对596个陈北洋的主题获取
用时3.252803325653076
这是对597个一位18世纪欧洲妇女着装的主题获取
用时3.1448733806610107
这是对598个许光汉黑白光影大片的主题获取
用时3.537571668624878
这是对599个爱的迫降终映宴的主题获取
用时3.1786739826202393
这是对600个全国第1例新冠肺炎逝世患者遗体解剖的主题获取
用时3.2537686824798584
这是对601个想见你大结局的主题获取
用时4.110823154449463
这是对602个雷神山院长称疫情拐点已经来到的主题获取
用时3.039997100830078
这是对603个爱奇艺崩了的主题获取
用

用时3.223404884338379
这是对773个上海警方查明武汉男子搭车来沪的主题获取
用时3.1473166942596436
这是对774个张鲁一演技的主题获取
用时3.0950989723205566
这是对775个寄生虫海报设计的主题获取
用时3.127901077270508
这是对776个小耳朵豪横的主题获取
用时3.1087677478790283
这是对777个警方20天收缴野生动物8万只的主题获取
这是对778个朴灿烈直播的主题获取
用时3.1687536239624023
这是对779个中央指导组对武汉疫情防控问题紧急约谈的主题获取
用时2.9581377506256104
这是对780个入沪通道首现后备箱藏人的主题获取
用时2.9909207820892334
这是对781个想见你团队声明的主题获取
用时3.175865650177002
这是对782个铁林黑化的主题获取
用时3.207223653793335
这是对783个十七月的黑牙的主题获取
用时2.7252094745635986
这是对784个企业复工要为职工配发口罩的主题获取
用时3.0015487670898438
这是对785个歌手延后录制的主题获取
用时3.01383638381958
这是对786个出门第一顿吃什么的主题获取
用时3.0562021732330322
这是对787个开电梯的N种方法的主题获取
用时3.7702882289886475
这是对788个宁夏治愈率5%的主题获取
这是对789个武汉疑似病人存量加速消化的主题获取
用时3.1436800956726074
这是对790个巴西发现神秘病毒的主题获取
用时3.119349479675293
这是对791个宅家的真实写照的主题获取
用时3.685286283493042
这是对792个湖北全省小区实行封闭式管理的主题获取
用时3.2968995571136475
这是对793个疫情期间妈妈说过最多的话的主题获取
用时2.985271453857422
这是对794个江苏援黄石医疗支援队出征的主题获取
用时3.0067248344421387
这是对795个韩国大邱将建造奉俊昊街的主题获取
用时3.0171191692352295
这是对796个普通人口罩可重复使用的主题获取
用时3.004855394

用时2.919167995452881
这是对964个294人涉疫情诈骗被抓的主题获取
用时2.9954469203948975
这是对965个天天向上的主题获取
用时3.1429288387298584
这是对966个李娜捐赠300万的主题获取
用时2.9550912380218506
这是对967个国家邮政局呼吁让快递员进小区的主题获取
用时2.9985504150390625
这是对968个水果姐中文为武汉加油的主题获取
用时3.047529935836792
这是对969个林忆莲的主题获取
用时3.1303911209106445
这是对970个上海发生两起聚集性疫情的主题获取
用时2.9282517433166504
这是对971个蔡敏敏贺灿阳的主题获取
用时3.134589910507202
这是对972个R1SE换预防疫情头像的主题获取
用时3.0347788333892822
这是对973个大火过后的澳大利亚的主题获取
用时3.1288089752197266
这是对974个瑞德西韦的主题获取
用时3.0417630672454834
这是对975个该追星的追星该追剧的追剧的主题获取
用时3.139540433883667
这是对976个原来东北的冰箱长这样的主题获取
用时3.0189456939697266
这是对977个山西查获假冒伪劣口罩10万只的主题获取
用时3.1165692806243896
这是对978个口罩喷酒精可能将病毒留在口罩上的主题获取
用时3.091114044189453
这是对979个电脑模拟仿真疫情趋势的主题获取
用时2.9238460063934326
这是对980个郑州复工时间的主题获取
用时3.0513906478881836
这是对981个最新疫情地图的主题获取
用时3.660123109817505
这是对982个在家不出门的娱乐方式的主题获取
用时5.431744813919067
这是对983个没有金韩彬的回归的主题获取
用时2.9580514430999756
这是对984个雷神山医院开展验收并逐步移交的主题获取
用时3.3794143199920654
这是对985个iPhone 汽车钥匙的主题获取
用时3.2265443801879883
这是对986个记者跟拍武汉居委会的一天的主题获取
用时2.91

用时2.954758644104004
这是对1150个成都1级地震的主题获取
用时2.8893942832946777
这是对1151个钟南山称疑似病例自行隔离非常危险的主题获取
用时3.048779010772705
这是对1152个目前已初步筛选出三种治疗药物的主题获取
用时3.0139410495758057
这是对1153个想见你直播的主题获取
用时3.166930913925171
这是对1154个白岩松对话温州市市长的主题获取
用时3.1519789695739746
这是对1155个邹韵好稳的主题获取
用时3.0206491947174072
这是对1156个湖北省特别是武汉市物资需要是重中之重的主题获取
用时3.3250622749328613
这是对1157个新增病例住在确诊病例楼上的主题获取
用时3.0635221004486084
这是对1158个地方不得以任何名义截留调用医疗物资的主题获取
用时2.892422676086426
这是对1159个湖北暂停办理所有婚姻登记业务的主题获取
用时2.9730234146118164
这是对1160个9省物资直达武汉协和的主题获取
用时3.0854525566101074
这是对1161个湖北省红十字工作人员的主题获取
用时2.9826345443725586
这是对1162个李兰娟院士带队出发驰援武汉的主题获取
用时2.9651951789855957
这是对1163个全明星致敬科比的主题获取
用时3.126805543899536
这是对1164个湖南4岁最小患者出院的主题获取
用时3.0530691146850586
这是对1165个央行将提供3000亿元专项再贷款的主题获取
用时3.0124893188476562
这是对1166个黑龙江 疫情期公职人员聚餐一律开除的主题获取
用时3.0839555263519287
这是对1167个双黄连的主题获取
用时3.074208974838257
这是对1168个武汉动物园的主题获取
用时3.055584192276001
这是对1169个野味disco的主题获取
用时3.0351345539093018
这是对1170个李文亮的主题获取
用时3.0178797245025635
这是对1171个刘亚仁声援武汉的主题获取
用时4.313193321

用时3.0366246700286865
这是对1336个什么是接触传播的主题获取
用时3.174356460571289
这是对1337个你平安归来我承包一年家务的主题获取
用时3.0266432762145996
这是对1338个石家庄悬赏举报武汉归来漏登人员的主题获取
用时2.9110217094421387
这是对1339个中国诗词大会第五季的主题获取
用时3.0937461853027344
这是对1340个最新疫情地图的主题获取
用时3.2573752403259277
这是对1341个诗词大会 王恒屹的主题获取
用时3.0399558544158936
这是对1342个财政部预拨疫情防控补助44亿元的主题获取
用时3.029010534286499
这是对1343个分离到三株新型冠状病毒毒株的主题获取
用时3.2883098125457764
这是对1344个台湾累计8例确诊新型肺炎的主题获取
用时3.221334457397461
这是对1345个河北推迟开学的主题获取
用时3.1195361614227295
这是对1346个北京小汤山的主题获取
用时3.1368601322174072
这是对1347个如何避免接触无症状的感染者的主题获取
用时3.176805257797241
这是对1348个终于明白古代禁足的感受的主题获取
用时2.923128128051758
这是对1349个诗词大会没有董卿的主题获取
用时3.0247435569763184
这是对1350个不会因春运返程出现大传染的主题获取
用时3.0528061389923096
这是对1351个武汉87岁婆婆治愈出院的主题获取
用时3.3164517879486084
这是对1352个钟南山强调目前不要出行的主题获取
用时3.1723132133483887
这是对1353个疫情1周或10天左右达到高峰的主题获取
用时3.0946834087371826
这是对1354个黄石原市长去世的主题获取
用时3.082045316696167
这是对1355个疫情死亡率会再降低的主题获取
用时3.0836572647094727
这是对1356个火神山医院效果图的主题获取
用时3.1189475059509277
这是对1357个超市买回的东西都要消毒吗的主题获取
用时2.98532319

用时3.1910789012908936
这是对1523个好电影不怕晚的主题获取
用时3.09995174407959
这是对1524个抗非典护士再战新型肺炎的主题获取
用时3.121037244796753
这是对1525个武汉确保加油站24小时营业的主题获取
用时3.0467193126678467
这是对1526个英国为武汉出发的直飞航班设立隔离区的主题获取
用时2.941406726837158
这是对1527个武汉新型肺炎防控指挥部第2号通告的主题获取
用时3.1544370651245117
这是对1528个冯薪朵的主题获取
用时3.106872797012329
这是对1529个李兰娟院士称普通民众暂不需要护目镜的主题获取
用时3.1216957569122314
这是对1530个湖南新增5例新型肺炎确诊病例的主题获取
用时2.9727206230163574
这是对1531个韩国首位变性士兵被开除的主题获取
用时2.8347766399383545
这是对1532个男版李子柒的主题获取
用时3.402031898498535
这是对1533个武汉封城的主题获取
用时3.1323046684265137
这是对1534个央视春晚两个分会场改为录播的主题获取
用时3.043144702911377
这是对1535个成都一公司车站免费发10万个口罩的主题获取
用时3.153594970703125
这是对1536个陌生女孩为执勤民警送口罩的主题获取
用时3.0298821926116943
这是对1537个医用外科口罩正确戴法的主题获取
用时3.0535759925842285
这是对1538个疫情地图的主题获取
用时3.0678040981292725
这是对1539个春节期间如何预防新型肺炎的主题获取
用时3.070657730102539
这是对1540个陈情令日本定档的主题获取
用时3.3287856578826904
这是对1541个17例新型肺炎死亡病例病情公布的主题获取
用时3.5025250911712646
这是对1542个春节最美逆行者的主题获取
用时2.929447889328003
这是对1543个新科娘的主题获取
用时2.9958345890045166
这是对1544个英国主持人怪声说中文被指种族歧视的主题获取
用时2.9376

In [17]:
theme.to_csv("theme.csv",encoding = "utf-8")

In [18]:
theme_new = pd.read_csv("theme.csv",usecols = [1,3])

In [15]:
theme_new

news_title                                         news_theme
0              0  #今天有话说#【肖战事件：没有胜利者的战争】德国慕尼黑大学法学博士吴一兴谈及肖战#227大团...
1              1  【#意大利新增566例新冠肺炎# #意大利累计确诊1694例新冠肺炎#】根据当地时间3月1日...
2              2  【#武磊造乌龙# 西班牙人领先马竞】西班牙人vs马德里竞技的比赛第24分钟，武磊传中造成萨维...
3              3     #上海老洋房##安家#\n有钱人的世界根本想象不到，1.5亿的上海老洋房，房似锦徐姑姑给我冲
4              4  【#深圳新增由英国途经香港输入病例#】据人民日报记者贺林平，3月1日凌晨，深圳市卫生健康委报...
...          ...                                                ...
1625        1649  #民民小调查#【#如何看待女厕设男童小便池#？】为了方便带孩子的母亲，杭州市第一人民医院在女...
1626        1650  【#境内确诊217例新型冠状病毒肺炎病例#】截至今日18时，我国境内累计报告新型冠状病毒感染...
1627        1651  钟南山院士今年83岁了，视频里根本看不出来！你知道吗，钟南山院士常年坚持运动，曾在1959年...
1628        1653  #想见你主演重回拍摄地# 9日晚，@施柏宇patrick 晒出与@許光漢GregHan @柯...
1629        1654  【钟南山：新型冠状病毒传染性与SARS如何比较？】钟南山：新型冠状病毒跟SARS病毒相比，尽...

[1630 rows x 2 columns]

# 评论爬取增加

因为上述的评论爬取时存在电脑死机等状况，故有些许热搜下的评论没有完全爬出来

In [4]:
resou_change = pd.read_csv("resou_change.csv",encoding = "GBK")
resou_new = resou_change.iloc[0:1655,]##取需要爬取的热搜

In [4]:
resou_id = list(resou_new[resou_new.review_len<100].id)#得到需要爬取的热搜id

In [11]:
new_driver = webdriver.Chrome()
pinglun = pd.DataFrame(columns = {"news_title","review"})
#i = 128 #序号，表示第几个热搜
k = 0
flag = 0 #表示重新开始一个session
for m in resou_id:
    time1 = time.time()
    title = resouList.news_title[m]
    if title =='（微博广告位留空）':
        continue
    print("这是对"+str(title)+"的评论获取")
    url = "https://s.weibo.com/weibo?q="+str(title)+"&xsort=hot&Refer=hotmore"
    try:
        new_driver.get(url)
    except:
        print("the url is error")
    #theme_len = len(new_driver.find_elements_by_class_name("card-wrap"))
    #resouList.at[i,'theme'] = new_driver.find_element_by_xpath("//*[@id='pl_feedlist_index']/div[2]/div[1]/div/div[1]/div[2]/p[2]").text
    #my_str = new_driver.find_element_by_xpath('//*[@id="pl_feedlist_index"]/div[2]/div[1]/div/div[2]/ul/li[3]/a').text    
   
    review_len = 200##只爬取前1000个评论信息    
    if(flag==0):
        time.sleep(5)
        new_driver.find_element_by_xpath('//*[@id="weibo_top_public"]/div/div/div[3]/div[2]/ul/li[3]/a').click()
        time.sleep(5)#等待着登录框跳出来
        new_driver.find_element_by_name('username').send_keys("18811399396")
        new_driver.find_element_by_name('password').send_keys("980zfl+-")
        new_driver.find_element_by_class_name('W_btn_a').click()
        flag = 1
        time.sleep(10)#等待着登录
    time.sleep(5)
    for section in range(1,5):
        try:
            new_driver.execute_script('window.scrollTo(0,1000)')
            new_driver.find_element_by_xpath('//*[@id="pl_feedlist_index"]/div[2]/div['+str(section)+']/div/div[2]/ul/li[3]/a').click()
            #print("到底有没有抓啊")
            time.sleep(3)
            new_driver.execute_script('window.scrollTo(0,1000)') 
            new_driver.find_element_by_xpath('//*[@id="pl_feedlist_index"]/div[2]/div['+str(section)+']/div/div[3]/div/div[3]/a/i').click()
        except:
            continue
        new_driver.execute_script('window.scrollTo(0,1000000)') 
        time.sleep(10)
        lens = len(new_driver.find_elements_by_class_name("list_li"))
        for j in range(review_len):
            pinglun.at[k,'news_title'] = m
            order = j+1
            try:
                print("这是第"+str(j)+"条评论")
                pinglun.at[k,'review'] = new_driver.find_element_by_xpath('//div[@node-type="comment_list"]/div['+str(order)+']/div[2]/div[1]').text
                k = k+1
            except:
                new_driver.execute_script('window.scrollTo(0,1000000)') 
                time.sleep(3)
                try:
                    new_driver.execute_script('window.scrollTo(0,1000000)')
                    time.sleep(3)
                    new_driver.find_element_by_class_name("more_txt").click()
                except:
                    break
            
        new_driver.get(url)            
    #i = i+1
    print("用时"+str(time.time()-time1))

这是对肖战工作室道歉的评论获取
这是第0条评论
这是第1条评论
这是第2条评论
这是第3条评论
这是第4条评论
这是第5条评论
这是第6条评论
这是第7条评论
这是第8条评论
这是第9条评论
这是第10条评论
这是第11条评论
这是第12条评论
这是第13条评论
这是第14条评论
这是第15条评论
这是第16条评论
这是第17条评论
这是第18条评论
这是第19条评论
这是第20条评论
这是第21条评论
这是第22条评论
这是第23条评论
这是第24条评论
这是第25条评论
这是第26条评论
这是第27条评论
这是第28条评论
这是第29条评论
这是第30条评论
这是第31条评论
这是第32条评论
这是第33条评论
这是第34条评论
这是第35条评论
这是第36条评论
这是第37条评论
这是第38条评论
这是第39条评论
这是第40条评论
这是第41条评论
这是第42条评论
这是第43条评论
这是第44条评论
这是第45条评论
这是第46条评论
这是第47条评论
这是第48条评论
这是第49条评论
这是第50条评论
这是第51条评论
这是第52条评论
这是第53条评论
这是第54条评论
这是第55条评论
这是第56条评论
这是第57条评论
这是第58条评论
这是第59条评论
这是第60条评论
这是第61条评论
这是第62条评论
这是第63条评论
这是第64条评论
这是第65条评论
这是第66条评论
这是第67条评论
这是第68条评论
这是第69条评论
这是第70条评论
这是第71条评论
这是第72条评论
这是第73条评论
这是第74条评论
这是第75条评论
这是第76条评论
这是第77条评论
这是第78条评论
这是第79条评论
这是第80条评论
这是第81条评论
这是第82条评论
这是第83条评论
这是第84条评论
这是第85条评论
这是第86条评论
这是第87条评论
这是第88条评论
这是第89条评论
这是第90条评论
这是第91条评论
这是第92条评论
这是第93条评论
这是第94条评论
这是第95条评论
这是第96条评论
这是第97条评论
这是第98条评论
这是第99条评论
这是第100条评论
这是第101条评论
这是第102条评论
这是第103条评论
这是第104条评论
这是第105条评论
这是第106条评论
这是第107条评论
这是第108条评论
这是第1

这是第47条评论
这是第48条评论
这是第49条评论
这是第50条评论
这是第51条评论
这是第52条评论
这是第53条评论
这是第54条评论
这是第55条评论
这是第56条评论
这是第57条评论
这是第58条评论
这是第59条评论
这是第60条评论
这是第61条评论
这是第62条评论
这是第63条评论
这是第64条评论
这是第65条评论
这是第66条评论
这是第67条评论
这是第68条评论
这是第69条评论
这是第70条评论
这是第71条评论
这是第72条评论
这是第73条评论
这是第74条评论
这是第75条评论
这是第76条评论
这是第77条评论
这是第78条评论
这是第79条评论
这是第80条评论
这是第81条评论
这是第82条评论
这是第83条评论
这是第84条评论
这是第85条评论
这是第86条评论
这是第87条评论
这是第88条评论
这是第89条评论
这是第90条评论
这是第91条评论
这是第92条评论
这是第93条评论
这是第94条评论
这是第95条评论
这是第96条评论
这是第97条评论
这是第98条评论
这是第99条评论
这是第100条评论
这是第101条评论
这是第102条评论
这是第103条评论
这是第104条评论
这是第105条评论
这是第106条评论
这是第107条评论
这是第108条评论
这是第109条评论
这是第110条评论
这是第111条评论
这是第112条评论
这是第113条评论
这是第114条评论
这是第115条评论
这是第116条评论
这是第117条评论
这是第118条评论
这是第119条评论
这是第120条评论
这是第121条评论
这是第122条评论
这是第123条评论
这是第124条评论
这是第125条评论
这是第126条评论
这是第127条评论
这是第128条评论
这是第129条评论
这是第130条评论
这是第131条评论
这是第132条评论
这是第133条评论
这是第134条评论
这是第135条评论
这是第136条评论
这是第137条评论
这是第138条评论
这是第139条评论
这是第140条评论
这是第141条评论
这是第142条评论
这是第143条评论
这是第144条评论
这是第145条评论
这是第146条评论
这是第147条评论
这是第148条评论
这是第149条评论
这是第150条评论
这是第151条评论
用时2

这是第175条评论
这是第176条评论
这是第177条评论
这是第178条评论
这是第179条评论
这是第180条评论
这是第181条评论
这是第182条评论
这是第183条评论
这是第184条评论
这是第185条评论
这是第186条评论
这是第187条评论
这是第188条评论
这是第189条评论
这是第190条评论
这是第191条评论
这是第192条评论
这是第193条评论
这是第194条评论
这是第195条评论
这是第196条评论
这是第197条评论
这是第198条评论
这是第199条评论
这是第0条评论
这是第1条评论
这是第2条评论
这是第3条评论
这是第4条评论
这是第5条评论
这是第6条评论
这是第7条评论
这是第8条评论
这是第9条评论
这是第10条评论
这是第11条评论
这是第12条评论
这是第13条评论
这是第14条评论
这是第15条评论
这是第16条评论
这是第17条评论
这是第18条评论
这是第19条评论
这是第20条评论
这是第21条评论
这是第22条评论
这是第23条评论
这是第24条评论
这是第25条评论
这是第26条评论
这是第27条评论
这是第28条评论
这是第29条评论
这是第30条评论
这是第31条评论
这是第32条评论
这是第33条评论
这是第34条评论
这是第35条评论
这是第36条评论
这是第37条评论
这是第38条评论
这是第39条评论
这是第40条评论
这是第41条评论
这是第42条评论
这是第43条评论
这是第44条评论
用时216.8091812133789
这是对深圳新增由英国途经香港输入病例的评论获取
这是第0条评论
这是第1条评论
这是第2条评论
这是第3条评论
这是第4条评论
这是第5条评论
这是第6条评论
这是第7条评论
这是第8条评论
这是第9条评论
这是第10条评论
这是第11条评论
这是第12条评论
这是第13条评论
这是第14条评论
这是第15条评论
这是第16条评论
这是第17条评论
这是第18条评论
这是第19条评论
这是第20条评论
这是第21条评论
这是第22条评论
这是第23条评论
这是第24条评论
这是第25条评论
这是第26条评论
这是第27条评论
这是第28条评论
这是第29条评论
这是第30条评论
这是第31条评论
这是第32条评论
这是第33条评论
这是第34条评论
这是第35条

这是第193条评论
这是第194条评论
这是第195条评论
这是第196条评论
这是第197条评论
这是第198条评论
这是第199条评论
这是第0条评论
这是第1条评论
这是第2条评论
这是第3条评论
这是第4条评论
这是第5条评论
这是第6条评论
这是第7条评论
这是第8条评论
这是第9条评论
这是第10条评论
这是第11条评论
这是第12条评论
这是第13条评论
这是第14条评论
这是第15条评论
这是第16条评论
这是第17条评论
这是第18条评论
这是第19条评论
这是第20条评论
这是第21条评论
这是第22条评论
这是第23条评论
这是第24条评论
这是第25条评论
这是第26条评论
这是第27条评论
这是第28条评论
这是第29条评论
这是第30条评论
这是第31条评论
这是第32条评论
这是第33条评论
这是第34条评论
这是第35条评论
这是第36条评论
这是第37条评论
这是第38条评论
这是第39条评论
这是第40条评论
这是第41条评论
这是第42条评论
这是第43条评论
这是第44条评论
这是第45条评论
这是第46条评论
这是第47条评论
这是第48条评论
这是第49条评论
这是第50条评论
这是第51条评论
这是第52条评论
这是第53条评论
这是第54条评论
这是第55条评论
这是第56条评论
这是第57条评论
这是第58条评论
这是第59条评论
这是第60条评论
这是第61条评论
这是第62条评论
这是第63条评论
这是第64条评论
这是第65条评论
这是第66条评论
这是第67条评论
这是第68条评论
这是第69条评论
这是第70条评论
这是第71条评论
这是第72条评论
这是第73条评论
这是第74条评论
这是第75条评论
这是第76条评论
这是第77条评论
这是第78条评论
这是第79条评论
这是第80条评论
这是第81条评论
这是第82条评论
这是第83条评论
这是第84条评论
这是第85条评论
这是第86条评论
这是第87条评论
这是第88条评论
这是第89条评论
这是第90条评论
这是第91条评论
这是第92条评论
这是第93条评论
这是第94条评论
这是第95条评论
这是第96条评论
这是第97条评论
这是第98条评论
这是第99条评论
这是第100条评论
这是第101条评论
这是第102条评论
这是第103条评论


这是第60条评论
这是第61条评论
这是第62条评论
这是第63条评论
这是第64条评论
这是第65条评论
这是第66条评论
这是第67条评论
这是第68条评论
这是第69条评论
这是第70条评论
这是第71条评论
这是第72条评论
这是第73条评论
这是第74条评论
这是第75条评论
这是第76条评论
这是第77条评论
这是第78条评论
这是第79条评论
这是第80条评论
这是第81条评论
这是第82条评论
这是第83条评论
这是第84条评论
这是第85条评论
这是第86条评论
这是第87条评论
这是第88条评论
这是第89条评论
这是第90条评论
这是第91条评论
这是第92条评论
这是第93条评论
这是第94条评论
这是第95条评论
这是第96条评论
这是第97条评论
这是第98条评论
这是第99条评论
这是第100条评论
这是第101条评论
这是第102条评论
这是第103条评论
这是第104条评论
这是第105条评论
这是第106条评论
这是第107条评论
这是第108条评论
这是第109条评论
这是第110条评论
这是第111条评论
这是第112条评论
这是第113条评论
这是第114条评论
这是第115条评论
这是第116条评论
这是第117条评论
这是第118条评论
这是第119条评论
这是第120条评论
这是第121条评论
这是第122条评论
这是第123条评论
这是第124条评论
这是第125条评论
这是第126条评论
这是第127条评论
这是第128条评论
这是第129条评论
这是第130条评论
这是第131条评论
这是第132条评论
这是第133条评论
这是第134条评论
这是第135条评论
这是第136条评论
这是第137条评论
这是第138条评论
这是第139条评论
这是第140条评论
这是第141条评论
这是第142条评论
这是第143条评论
这是第144条评论
这是第145条评论
这是第146条评论
这是第147条评论
这是第148条评论
这是第149条评论
这是第150条评论
这是第151条评论
这是第152条评论
这是第153条评论
这是第154条评论
这是第155条评论
这是第156条评论
这是第157条评论
这是第158条评论
这是第159条评论
这是第160条评论
这是第161条评论
这是第162条评论
这是第163条评论


...

这是第11条评论
这是第12条评论
这是第13条评论
这是第14条评论
这是第15条评论
用时217.0133237838745
这是对让女孩子都羡慕的身材的评论获取
这是第0条评论
这是第1条评论
这是第2条评论
这是第3条评论
这是第4条评论
这是第5条评论
这是第6条评论
这是第7条评论
这是第8条评论
这是第9条评论
这是第10条评论
这是第11条评论
这是第12条评论
这是第13条评论
这是第14条评论
这是第15条评论
这是第16条评论
这是第17条评论
这是第18条评论
这是第19条评论
这是第20条评论
这是第21条评论
这是第22条评论
这是第23条评论
这是第24条评论
这是第25条评论
这是第26条评论
这是第27条评论
这是第28条评论
这是第29条评论
这是第30条评论
这是第31条评论
这是第32条评论
这是第33条评论
这是第34条评论
这是第35条评论
这是第36条评论
这是第37条评论
这是第38条评论
这是第39条评论
这是第40条评论
这是第41条评论
这是第42条评论
这是第43条评论
这是第44条评论
这是第45条评论
这是第46条评论
这是第47条评论
这是第48条评论
这是第49条评论
这是第50条评论
这是第51条评论
这是第52条评论
这是第53条评论
这是第54条评论
这是第55条评论
这是第56条评论
这是第57条评论
这是第58条评论
这是第59条评论
这是第60条评论
这是第61条评论
这是第62条评论
这是第63条评论
这是第64条评论
这是第65条评论
这是第66条评论
这是第67条评论
这是第68条评论
这是第69条评论
这是第70条评论
这是第71条评论
这是第72条评论
这是第73条评论
这是第74条评论
这是第75条评论
这是第76条评论
这是第77条评论
这是第78条评论
这是第79条评论
这是第80条评论
这是第81条评论
这是第82条评论
这是第83条评论
这是第84条评论
这是第85条评论
这是第86条评论
这是第87条评论
这是第88条评论
这是第89条评论
这是第90条评论
这是第91条评论
这是第92条评论
这是第93条评论
这是第94条评论
这是第95条评论
这是第96条评论
这是第97条评论
这是第98条评论
这是第99条评论
这是第100条评论
这是第101条评论
这是第102

这是第44条评论
这是第45条评论
这是第46条评论
这是第47条评论
这是第48条评论
这是第49条评论
这是第50条评论
这是第51条评论
这是第52条评论
这是第53条评论
这是第54条评论
这是第55条评论
这是第56条评论
这是第57条评论
这是第58条评论
这是第59条评论
这是第60条评论
这是第61条评论
这是第62条评论
这是第63条评论
这是第64条评论
这是第65条评论
这是第66条评论
这是第67条评论
这是第68条评论
这是第69条评论
这是第70条评论
这是第71条评论
这是第72条评论
这是第73条评论
这是第74条评论
这是第75条评论
这是第76条评论
这是第77条评论
这是第78条评论
这是第79条评论
这是第80条评论
这是第81条评论
这是第82条评论
这是第83条评论
这是第84条评论
这是第85条评论
这是第86条评论
这是第87条评论
这是第88条评论
这是第89条评论
这是第90条评论
这是第91条评论
这是第92条评论
这是第93条评论
这是第94条评论
这是第95条评论
这是第96条评论
这是第97条评论
这是第98条评论
这是第99条评论
这是第100条评论
这是第101条评论
这是第102条评论
这是第103条评论
这是第104条评论
这是第105条评论
这是第106条评论
这是第107条评论
这是第108条评论
这是第109条评论
这是第110条评论
这是第111条评论
这是第112条评论
这是第113条评论
这是第114条评论
这是第115条评论
这是第116条评论
这是第117条评论
这是第118条评论
这是第119条评论
这是第120条评论
这是第121条评论
这是第122条评论
这是第123条评论
这是第124条评论
这是第125条评论
这是第126条评论
这是第127条评论
这是第128条评论
这是第129条评论
这是第130条评论
这是第131条评论
这是第132条评论
这是第133条评论
这是第134条评论
这是第135条评论
这是第136条评论
这是第137条评论
这是第138条评论
这是第139条评论
这是第140条评论
这是第141条评论
这是第142条评论
这是第143条评论
这是第144条评论
这是第145条评论
这是第146条评论
这是第147条评论
这是第148条评论
这是第149

这是第105条评论
这是第106条评论
这是第107条评论
这是第108条评论
这是第109条评论
这是第110条评论
这是第111条评论
这是第112条评论
这是第113条评论
这是第114条评论
这是第115条评论
这是第116条评论
这是第117条评论
这是第118条评论
这是第119条评论
这是第120条评论
这是第121条评论
这是第122条评论
这是第123条评论
这是第124条评论
这是第125条评论
这是第126条评论
这是第127条评论
这是第128条评论
这是第129条评论
这是第130条评论
这是第131条评论
这是第132条评论
这是第133条评论
这是第134条评论
这是第135条评论
这是第136条评论
这是第137条评论
这是第138条评论
这是第139条评论
这是第140条评论
这是第141条评论
这是第142条评论
这是第143条评论
这是第144条评论
这是第145条评论
这是第146条评论
这是第147条评论
这是第148条评论
这是第149条评论
这是第150条评论
这是第151条评论
这是第152条评论
这是第153条评论
这是第154条评论
这是第155条评论
这是第156条评论
这是第157条评论
这是第158条评论
这是第159条评论
这是第160条评论
这是第161条评论
这是第162条评论
这是第163条评论
这是第164条评论
这是第165条评论
这是第166条评论
这是第167条评论
这是第168条评论
这是第169条评论
这是第170条评论
这是第171条评论
这是第172条评论
这是第173条评论
这是第174条评论
这是第175条评论
这是第176条评论
这是第177条评论
这是第178条评论
这是第179条评论
这是第180条评论
这是第181条评论
这是第182条评论
这是第183条评论
这是第184条评论
这是第185条评论
这是第186条评论
这是第187条评论
这是第188条评论
这是第189条评论
这是第190条评论
这是第191条评论
这是第192条评论
这是第193条评论
这是第194条评论
这是第195条评论
这是第196条评论
这是第197条评论
这是第198条评论
这是第199条评论
用时245.11193132400513
这是对武汉再建10座方舱医院的评论获取
这是第0条评论
这

这是第26条评论
这是第27条评论
这是第28条评论
这是第29条评论
这是第30条评论
这是第31条评论
这是第32条评论
这是第33条评论
这是第34条评论
这是第35条评论
这是第36条评论
这是第37条评论
这是第38条评论
这是第39条评论
这是第40条评论
这是第41条评论
这是第42条评论
这是第43条评论
这是第44条评论
这是第45条评论
这是第46条评论
这是第47条评论
这是第48条评论
这是第49条评论
这是第50条评论
这是第51条评论
这是第52条评论
这是第53条评论
这是第54条评论
这是第55条评论
这是第56条评论
这是第57条评论
这是第58条评论
这是第59条评论
这是第60条评论
这是第61条评论
这是第62条评论
这是第63条评论
这是第64条评论
这是第65条评论
这是第66条评论
这是第67条评论
这是第68条评论
这是第69条评论
这是第70条评论
这是第71条评论
这是第72条评论
这是第73条评论
这是第74条评论
这是第75条评论
这是第76条评论
这是第77条评论
这是第78条评论
这是第79条评论
这是第80条评论
这是第81条评论
这是第82条评论
这是第83条评论
这是第84条评论
这是第85条评论
这是第86条评论
这是第87条评论
这是第88条评论
这是第89条评论
这是第90条评论
这是第91条评论
这是第92条评论
这是第93条评论
这是第94条评论
这是第95条评论
这是第96条评论
这是第97条评论
这是第98条评论
这是第99条评论
这是第100条评论
这是第101条评论
这是第102条评论
这是第103条评论
这是第104条评论
这是第105条评论
这是第106条评论
这是第107条评论
这是第108条评论
这是第109条评论
这是第110条评论
这是第111条评论
这是第112条评论
这是第113条评论
这是第114条评论
这是第115条评论
这是第116条评论
这是第117条评论
这是第118条评论
这是第119条评论
这是第120条评论
这是第121条评论
这是第122条评论
这是第123条评论
这是第124条评论
这是第125条评论
这是第126条评论
这是第127条评论
这是第128条评论
这是第129条评论
这是第130条评论
这是第131条评论
这是第132条评论
这是第1

KeyboardInterrupt: 

In [13]:
pinglun.to_csv("pinglun_new.csv")